# Tax Calculations for financial year ending in 31st March 2024 #

In [1]:
#pip install quiffen
#pip install openpyxl
#pip install xlrd


In [2]:
import pandas as pd
import numpy as np
from quiffen import Qif

In [3]:
from datetime import date
#from dotenv import load_dotenv
#from airtable.airtable import Airtable

In [4]:
#load_dotenv()
#AIRTABLE_APIKEY = os.environ.get("AIRTABLE_APIKEY")

In [5]:
import warnings
warnings.filterwarnings('ignore')

## Online Expenses ##

## Depreciation ##

### Compute Depreciation on HP ProBook Laptop used for work ###

In [6]:
df = pd.read_excel('HP-ProBook-650-G4-depreciation.xlsx', skiprows=12)
df


Year ending 31 March  Opening value Depreciation rate  \
0                  2023        1898.00            50% DV   
1                  2024        1502.59            50% DV   
2                  2025         751.30            50% DV   

   Depreciation for year  Closing value  Business use  Claim as tax deduction  
0                 395.41        1502.59          0.95                  375.63  
1                 751.29         751.30          0.95                  713.72  
2                 375.65         375.65          0.95                  356.86

In [7]:
#iloc seems to be needed now to get a float out of it
notebookDepreciation = float(df[df['Year ending 31 March']==2024]['Claim as tax deduction'].iloc[0])
notebookDepreciation

713.72

## ASB Expenses ##

In [8]:
qif = Qif.parse('asb-00.qif', day_first=False)
acc = qif.accounts['Quiffen Default Account']

In [9]:
asb00 = qif.to_dataframe()[['date', 'memo', 'payee', 'amount', 'check_number', 'line_number' ]]
#asb00.head()

In [10]:
qif = Qif.parse('asb-50.qif', day_first=False)
acc = qif.accounts['Quiffen Default Account']

In [11]:
asb50 = qif.to_dataframe()[['date', 'memo', 'payee', 'amount', 'check_number', 'line_number' ]]
#asb50.head()

No expenses claimed as a result of ASB accounts

### Co-Operative Bank Accounts ###

In [12]:
qif = Qif.parse('02-1248-0836615-001_01Apr2023_31Mar2024.Qif', day_first=False)
acc = qif.accounts['Quiffen Default Account']

In [13]:
coop001 = qif.to_dataframe()[['date', 'memo', 'payee', 'amount', 'check_number', 'line_number' ]]
coop001.head()

date                               memo payee  amount check_number  \
0 2024-03-31        EFTPOS BEACHLENDS SUPERETTE  None  -19.00         None   
1 2024-03-27          EFTPOS WOOLWORTHS NZ 9177  None  -64.22         None   
2 2024-03-26    DC- WEBQUEST LIMITED INV-1803-2  None  320.00         None   
3 2024-03-26  TRANSACTION FEES - 26/02 TO 25/03  None   -3.50         None   
4 2024-03-23          EFTPOS WOOLWORTHS NZ 9177  None  -22.19         None   

   line_number  
0            1  
1            7  
2           13  
3           19  
4           25

In [14]:
#coop001['memo'].unique()

## Co-op Account Income & Expenses ##

In [15]:
qif = Qif.parse('02-1248-0836615-002_01Apr2023_31Mar2024.Qif', day_first=False)
acc = qif.accounts['Quiffen Default Account']

In [16]:
coop002 = qif.to_dataframe()[['date', 'memo', 'payee', 'amount', 'check_number', 'line_number' ]]
# coop002.head()

In [17]:
adblock = np.abs(coop002[coop002['memo'].str.contains("ADBLO")]['amount'].sum())
adblock

22.8

In [18]:
# Find the amount paid for the Bose Noise Cancelling headphones.  Essential to maintain a 
# quiet office environment free from distractions.

bose_headphones = np.abs(coop002[coop002['memo'].str.contains('Bose', case=False)]['amount'].sum())
coop002[coop002['memo'].str.contains('Bose', case=False)]

date                    memo payee  amount check_number  line_number
134 2023-05-30  POS PAYPAL *BOSEPTYLTD  None -499.95         None          805

In [19]:
bose_headphones

499.95

In [20]:
# Compute the amount spent on the Talk360 internet to phone service  ( negative indicates expense )
talk360 = np.abs(coop001[coop001.memo.str.contains('talk360')]['amount'].sum())
talk360

25.0

In [21]:
# Sole source of Income
webquest = coop001[coop001.memo.str.contains('webquest', case=False)].count()['date']
total_webquest = webquest *320
total_webquest

7040

In [22]:
#coop002.memo.unique()

In [23]:
spark_mobile = np.abs(coop002[coop002.memo.str.contains('spark', case=False)]['amount'].sum())
spark_mobile


286.0

In [24]:
ramnode = np.abs(coop002[coop002.memo.str.contains('ramnode', case=False)]['amount'].sum())
ramnode


239.47

In [25]:
bose_headphones

499.95

## Calculate 20% of board as office space ##

I moved back to Whanganui 24th April 2022

In [26]:
num_board_pay_periods = int((date(2023,3,31) - date(2022, 4, 24)).days / 7)
num_board_pay_periods

48

In [27]:
total_board_paid = num_board_pay_periods * 240
total_board_paid

11520

## Final Calculation ##

### Total Income ###

In [28]:
total_income = total_webquest
total_income

7040

### Total Expenses ###

In [29]:
dct = {"Spark Mobile":spark_mobile, 
      'Ramnode VPS': ramnode, "HP ProBook 650 G4 Depreciation":notebookDepreciation, 
       'Bose Headphones': bose_headphones,
       'Talk360 internet service': talk360,
       'Ad Blocker': adblock,
       '20% of board as office space':total_board_paid*.20}
df = pd.Series(dct)
df

Spark Mobile                       286.00
Ramnode VPS                        239.47
HP ProBook 650 G4 Depreciation     713.72
Bose Headphones                    499.95
Talk360 internet service            25.00
Ad Blocker                          22.80
20% of board as office space      2304.00
dtype: float64

In [30]:
total_expenses = df.sum()
total_expenses

4090.94

### Net Income ###

In [31]:
total_income - total_expenses

2949.06